In [1]:
!pip install nglview --user                   

In [2]:
import nglview as nv
import requests         # Этот стандартный модуль позволяет посылать запросы к веб-ресурсам
import json             # Этот стандартный модуль позволяет легко работать с текстовым форматом json

In [3]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [4]:
keyword_clause = {
    "type": "terminal",
    "service": "full_text", # искать во всех текстовых полях 
    "parameters": {
        "value": "androgen receptor with testosterone" # ключевые слова
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [5]:
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.5,  # Какое разрешение: не хуже 2.5 ангстрем
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [6]:
# Сколько лигандов должно быть в записи: не меньше 1 (то есть больше 0)

has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [7]:
# Дата публикации записи: с января 2005 по январь 2010 года

date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2005-01-01", # год-месяц-день
            "to": "2010-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [8]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v2/query'

json_query = json.dumps(my_query) 

search = requests.post(f'{rcsb}', data=json_query) # Отсылаем запрос

In [9]:
search # проверка (200 - значит хорошо)

<Response [200]>

In [10]:
search_result = search.json() # Распаковываем ответ сервера в словарь
search_result                 # Берём лучшую находку

{'query_id': '717eccea-4aa6-438d-a4da-5051de3df35b',
 'result_type': 'entry',
 'total_count': 16514,
 'result_set': [{'identifier': '2AM9', 'score': 0.9867492062372719},
  {'identifier': '2Q7I', 'score': 0.9857518477206042},
  {'identifier': '2Q7K', 'score': 0.985729945544985},
  {'identifier': '2Q7L', 'score': 0.982568026943184},
  {'identifier': '2Q7J', 'score': 0.9817502033034597},
  {'identifier': '2AMA', 'score': 0.9784848902422165},
  {'identifier': '2IHQ', 'score': 0.9603377009659534},
  {'identifier': '2PNU', 'score': 0.9572375761820181},
  {'identifier': '2AMB', 'score': 0.9553533144737761},
  {'identifier': '1Z95', 'score': 0.9530152684698528}]}

In [11]:
best_hit = search_result["result_set"][0] # Лучшая находка
best_hit

{'identifier': '2AM9', 'score': 0.9867492062372719}

ЗАДАНИЕ 2: Таким образом, я далее буду работать с PDB ID 2AM9. На сайте RCSB PDBпод этим идентификатором была найдена "Кристаллическая структура лигандсвязывающего домена рецептора андрогена человека в комплексе с тестостероном(ключевые слова из запроса в заголовке)"(рецептор из организма человека; экспресирован  Escherichia coli).Андрогены оказывают свое действие путем связывания с высокоспецифичным рецептором андрогена (AR). В дополнение к природным мощным андрогенам, AR связывает множество синтетических молекул-агонистов или антагонистов с различным сродством. Сама структура лиганда (размер, наличие и положение ненасыщенных связей, которые влияют на геометрию стероидного ядра или электронные свойства соседних атомов и т.д.) определяет количество взаимодействий, которые он может осуществлять с hARLBD( лигандсвязывающего домена рецептора андрогена человека ).

In [12]:
from ipywidgets import interact, fixed

my_examples = {
    'Вариант 1': {
        'description': '''
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде rope красного цвета
Боковые радикалы в стержневой модели, покрашенные согласно элементу
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам
''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity': 0.1
                 }
            },
            {
                'type': 'rope',
                'params': {
                    'sele': 'protein',                 
                    'color': 'red'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
        ],
    },
    'Вариант 5': {
        'description': '''
Белок в виде tube, покраска по типу вторичной структуры
Боковые радикалы в стержневой модели, покрашены по гидрофобности
Лиганды показаны линиями, покрашены по элементам
Вода и ионы показаны в виде Ван-дер-Ваальсовых сфер

''',
        'representations': [
            {
                'type': 'tube',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'sstruc'
                 }
            },
            {
                'type': 'line',
                'params': {
                    'sele': 'ligand',                 
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'hydrophobicity'  
                 }
            },
            {
              'type':'spacefill',
              'params': {
                  'sele':'water or ion'
              }
            },
        ],
    },
    'Вариант 10': {
        'description': '''
Белок в виде cartoon белого цвета
Cartoon для остатков с 20-го по 55-й покрашен в зеленый
Для остатков с 20-го по 55-й показаны боковые радикалы в модели hyperball, покраска по элементам
Лиганды показаны в шаростержневой модели, покраска по элементам

''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white'
                 }
            },
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein and 20-55',               
                    'color': 'green'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'sidechainAttached and 20-55',               
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',
                'params': {
                    'sele': 'ligand',                 
                    'color': 'element'  
                 }
            },
        ],
    },
}

In [13]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("2am9", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Вариант 1', 'Вариант 5', 'Вариант 10'), v…

NGLWidget()